In [200]:
# imports
import json
from collections import defaultdict, Counter

In [242]:
# get level hierarchy
levels = {}
levels_reversed = defaultdict(set)
children = defaultdict(list)
parents = {}
with open("all_fields_hierarchy.jsonl", "r") as json_file:
    data = [json.loads(line) for line in json_file]
for row in data:
    levels[row["child_display_name"].lower()] = int(row["child_level"])
    levels_reversed[int(row["child_level"])].add(row["child_display_name"].lower())
    if row["parent_level"] == 0:
        levels[row["display_name"].lower()] = row["parent_level"]
        levels_reversed[row["parent_level"]].add(row["display_name"].lower())
    children[row["display_name"].lower()].append(row["child_display_name"].lower())
    parents[row["child_display_name"].lower().strip()] = row["display_name"].lower().strip()

In [21]:
# quick way to read a big json file but not read it all at once
def read_yield_json(filename):
    with open(filename, 'r') as infile:
        for line in infile:
            if not line:
                continue
            yield json.loads(line)

In [62]:
# getting just the very top field
i = 0
top_fields = {}
for row in read_yield_json("../../assets/venues/out/en_scores.jsonl"):
    max_dict = defaultdict(int)
    field_dict = {}
    for field in row["fields"]:
        level = levels[field["id"].lower()]
        if field["score"] > max_dict[level]:
            field_dict[level] = field["id"].lower()
            max_dict[level] = field["score"]
    top_fields[row["merged_id"]] = field_dict
    i += 1

In [92]:
# check which fields match when looking at just top field
missing = []
matches = Counter()
non_matches = Counter()
non_match_fields = defaultdict(Counter)
comparable_fields_counts = Counter()
for row in read_yield_json("../../assets/venues/en_venue_fos.jsonl"):
    field_level = levels[row["fos"]]
    # if there was no text we didn't predict so it doesn't appear
    if row["merged_id"] in top_fields:
        # print("predicted: ", top_fields[row["merged_id"]][field_level], ", expected: ", row["fos"])
        if row["fos"] == top_fields[row["merged_id"]][field_level]:
            matches[row["fos"]] += 1
        elif row["fos"] in comparable_fields and top_fields[row["merged_id"]][field_level] in comparable_fields[row["fos"]]:
            comparable_fields_counts[row["fos"]] += 1
        else:
            non_matches[row["fos"]] += 1
            non_match_fields[row["fos"]][top_fields[row["merged_id"]][field_level]] += 1
    else:
        missing.append(row["merged_id"])

predicted:  cryptography , expected:  hardware security
predicted:  reverse engineering , expected:  reverse engineering
predicted:  machine translation , expected:  machine translation
predicted:  imaging genetics , expected:  generative models
predicted:  machine translation , expected:  machine translation
predicted:  machine translation , expected:  machine translation
predicted:  machine translation , expected:  machine translation
predicted:  machine translation , expected:  machine translation
predicted:  neuroscience of multilingualism , expected:  generative models
predicted:  machine translation , expected:  machine translation
predicted:  language model , expected:  generative models
predicted:  regulation of artificial intelligence , expected:  ethics of artificial intelligence
predicted:  language model , expected:  generative models
predicted:  machine translation , expected:  machine translation
predicted:  learning to rank , expected:  machine translation
predicted:  ma

IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)



 machine learning , expected:  machine learning
predicted:  machine learning , expected:  machine learning
predicted:  machine learning , expected:  machine learning
predicted:  machine learning , expected:  machine learning
predicted:  machine learning , expected:  machine learning
predicted:  machine learning , expected:  machine learning
predicted:  game theory , expected:  machine learning
predicted:  reinforcement learning , expected:  machine learning
predicted:  machine learning , expected:  machine learning
predicted:  natural language processing , expected:  machine learning
predicted:  machine learning , expected:  machine learning
predicted:  machine learning , expected:  machine learning
predicted:  neurophysiology , expected:  machine learning
predicted:  reinforcement learning , expected:  machine learning
predicted:  viral dynamics , expected:  machine learning
predicted:  machine learning , expected:  machine learning
predicted:  reinforcement learning , expected:  mach

IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)



predicted:  speech recognition , expected:  speech recognition
predicted:  speech recognition , expected:  speech recognition
predicted:  speech recognition , expected:  speech recognition
predicted:  machine learning , expected:  speech recognition
predicted:  speech recognition , expected:  speech recognition
predicted:  speech recognition , expected:  speech recognition
predicted:  structural bioinformatics , expected:  speech recognition
predicted:  speech recognition , expected:  speech recognition
predicted:  speech recognition , expected:  speech recognition
predicted:  speech recognition , expected:  speech recognition
predicted:  speech recognition , expected:  speech recognition
predicted:  speech recognition , expected:  speech recognition
predicted:  speech recognition , expected:  speech recognition
predicted:  speech recognition , expected:  speech recognition
predicted:  data science , expected:  speech recognition
predicted:  machine learning , expected:  speech recogni

IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)



In [170]:
# check matches vs. non-matches vs. comparable fields
for i in matches:
    print(i, ",", matches[i], ",", comparable_fields_counts[i], ",", non_matches[i])

reverse engineering , 491 , 188 , 223
machine translation , 766 , 0 , 134
ethics of artificial intelligence , 186 , 302 , 89
post-quantum cryptography , 205 , 23 , 50
hardware security , 253 , 0 , 227
integrated circuit design , 292 , 0 , 430
fairness , 164 , 197 , 56
immunotoxicology , 142 , 462 , 93
oncogenomics , 18 , 5 , 11
biomedical engineering , 92 , 0 , 1060
euv lithography , 455 , 24 , 58
generative models , 6 , 355 , 493
oncolytic virus , 65 , 3 , 1
homomorphic encryption , 28 , 5 , 3
ellipsometry , 7 , 0 , 7
fuzzing , 27 , 0 , 3
biometrics , 141 , 0 , 383
traffic analysis , 24 , 48 , 56
neurogenetics , 7 , 8 , 2
mems , 1793 , 1406 , 2177
biofuel , 625 , 1362 , 494
genomics , 3430 , 5827 , 1189
robotics , 31880 , 8790 , 1978
photomask , 738 , 988 , 361
cryptography , 3186 , 300 , 425
metabolomics , 1756 , 152 , 222
biostatistics , 792 , 94 , 554
computer vision , 27492 , 11271 , 1055
immunopathology , 482 , 1044 , 256
machine learning , 13949 , 847 , 1002
microlithography , 2

In [190]:
# see the most common non-match fields
for i in non_match_fields:
    print(i, "   ", non_match_fields[i].most_common(10))

hardware security     [('integrated circuit design', 100), ('cryptography', 97), ('internet security', 92), ('network security', 59), ('language-based security', 58), ('machine learning', 37), ('core ip', 36), ('eda software', 34), ('semiconductor device fabrication', 23), ('application security', 19)]
generative models     [('text mining', 82), ('biomedical text mining', 55), ('parsing', 49), ('knowledge representation and reasoning', 49), ('information extraction', 48), ('semantic parsing', 47), ('algorithmic bias', 38), ('deep learning', 32), ('biostatistics', 28), ('question answering', 28)]
machine translation     [('language model', 44), ('multi-task learning', 41), ('deep learning', 18), ('self-supervised learning', 17), ('ensemble learning', 14), ('learning to rank', 13), ('collaborative filtering', 11), ('automatic summarization', 11), ('sequence alignment', 10), ('document classification', 10)]
integrated circuit design     [('core ip', 124), ('eda software', 92), ('computer 

In [81]:
# make a dict of comparable fields
comparable_fields = {}

In [84]:
# manually add comparable fields
comparable_fields["ethics of artificial intelligence"] = {"fairness", "regulation of artificial intelligence", "algorithmic bias", "ai safety", "explainable artificial intelligence"}
comparable_fields["generative models"] = {"language model", "automatic summarization", "dialogue systems", "procedural generation"}
comparable_fields["fairness"] = {"ethics of artificial intelligence", "regulation of artificial intelligence", "algorithmic bias", "ai safety", "explainable artificial intelligence"}
comparable_fields["reverse engineering"] = {"static program analysis", "program analysis", "arbitrary code execution"}
comparable_fields["immunotoxicology"] = {"immunomics", "immunotherapy", "immunopathology", "clinical immunology"}
comparable_fields["oncogenomics"] = {"gene therapy", "cancer systems biology", "cancer epigenetics", "viral oncogenesis", "cancer immunotherapy"}
comparable_fields["euv lithography"] = {"next-generation lithography", "lithography stepper"}
comparable_fields["post-quantum cryptography"] = {"encryption", "public-key cryptography"}
comparable_fields["traffic analysis"] = {"mobile security", "network assurance", "web tracking", "session hijacking"}
comparable_fields["homomorphic encryption"] = {"secure multi-party computation", "cryptographic protocols", "encryption"}
comparable_fields["oncolytic virus"] = {"cancer immunotherapy", "viral vectors"}
comparable_fields["neurogenetics"] = {"medical genetics", "clinical neuroscience"}
comparable_fields["mems"] = {"atomic force microscopy", "active-pixel sensor", "mosfet", "sensor fusion"}
comparable_fields["biofuel"] = {"industrial fermentation", "industrial enzymes", "bioenergy", "cell engineering", "microbial biodegradation", "biomass"}
comparable_fields["genomics"] = {"immunomics", "transcriptomics", "proteomics", "molecular genetics"}
comparable_fields["robotics"] = {"computer vision", "machine learning", "reinforcement learning"}
comparable_fields["photomask"] = {"resolution enhancement technologies", "optical proximity correction", "mask inspection", "phase-shift mask", "multiple patterning", "lithography stepper"}
comparable_fields["cryptography"] = {"internet security", "hardware security", "information privacy", "network security"}
comparable_fields["metabolomics"] = {"lipidomics", "immunomics", "proteomics"}
comparable_fields["biostatistics"] = {"gene expression profiling", "biomarker", "personalized medicine"}
comparable_fields["computer vision"] = {"machine learning", "reinforcement learning"}
comparable_fields["immunopathology"] = {"immunotherapy", "clinical immunology", "viral pathogenesis", "immunomics", "developmental immunology", "classical immunology", "synthetic immunology"}
comparable_fields["machine learning"] = {"reinforcement learning", "computer vision", "speech recognition", "data science", "data mining", "natural language processing"}
comparable_fields["microlithography"] = {"photolithography", "nanolithography", "3d microfabrication", "microfabrication", "semiconductor device fabrication", "etching"}
comparable_fields["immunohaematology"] = {"molecular immunology", "humoral immunology", "autoimmunity"}
comparable_fields["neuropharmacology"] = {"molecular neuroscience", "cellular neuroscience", "neuroendocrinology", "neurochemistry", "cognitive neuroscience", "neuroanatomy", "affective neuroscience"}
comparable_fields["synthetic biology"] = {"gene expression", "cell engineering", "directed evolution", "artificial gene synthesis", "tissue engineering"}
comparable_fields["speech recognition"] = {"machine learning", "natural language processing", "reinforcement learning"}
comparable_fields["computer simulation"] = {"general game playing", "human-based computation game", "behavioral game theory", "active learning", "transfer learning", "negotiation theory"} 
comparable_fields["genetic programming"] = {"evolutionary computation", "mathematical optimization", "metaheuristics", "feature selection", "online machine learning", "ensemble learning"}
comparable_fields["human-robot interaction"] = {"robot locomotion", "cognitive robotics", "robotic mapping", "robot learning", "gesture recognition", "vehicular automation", "robotic sensing", "human-computer interaction", "robot localization"}
comparable_fields["biomechanical engineering"] = {"tissue engineering", "neuromechanics", "molecular dynamics", "biomedical instrumentation", "biomaterials"}
comparable_fields["agricultural biotechnology"] = {"biomolecular engineering", "biochemical and bioproducts engineering", "plant genetics", "microbial genetics", "environmental biotechnology"} 
comparable_fields["natural language processing"] = {"machine learning", "speech recognition", "knowledge management", "reinforcement learning", "data mining"} 

In [103]:
# get top 5 fields
i = 0

for row in read_yield_json("../../assets/venues/out/en_scores.jsonl"):
    max_dict = defaultdict(list)
    field_dict = {}
    for field in row["fields"]:
        level = levels[field["id"].lower()]
        max_dict[level].append((field["score"], field["id"]))
    for level in max_dict:
        top_five_fields = sorted(max_dict[level], reverse=True)[:5]
        field_dict[level] = [i[1].lower() for i in top_five_fields]
    top_fields[row["merged_id"]] = field_dict
    i += 1

In [158]:
# check which fields match when looking at multiple top fields
missing = []
matches = Counter()
non_matches = Counter()
non_match_fields = defaultdict(Counter)
comparable_fields_counts = Counter()
for row in read_yield_json("../../assets/venues/en_venue_fos.jsonl"):
    field_level = levels[row["fos"]]
    # if there was no text we didn't predict so it doesn't appear
    if row["merged_id"] in top_fields:
        comparable = False
        matched = False
        # print("predicted: ", top_fields[row["merged_id"]][field_level], ", expected: ", row["fos"])
        if row["fos"] in top_fields[row["merged_id"]][field_level]:
            matches[row["fos"]] += 1
            matched = True
        else: 
            if row["fos"] in comparable_fields:
                for comparable_field in comparable_fields[row["fos"]]:
                    if comparable_field in top_fields[row["merged_id"]][field_level]:
                        comparable = True
        if comparable:
            comparable_fields_counts[row["fos"]] += 1
        elif not matched:
            non_matches[row["fos"]] += 1
            for non_match_field in top_fields[row["merged_id"]][field_level]:
                non_match_fields[row["fos"]][non_match_field] += 1
    else:
        missing.append(row["merged_id"])

In [171]:
# check matches vs. non-matches vs. comparable fields
total_matched = 0
total_comparable = 0
total_not_matched = 0
percentage_matched = []
percentage_matched_or_comparable = []
percentage_not_matched = []
for i in matches:
    total_matched += matches[i]
    total_comparable += comparable_fields_counts[i]
    total_not_matched += non_matches[i]
    percentage_matched.append(matches[i] / (matches[i] + comparable_fields_counts[i] + non_matches[i]))
    percentage_matched_or_comparable.append((matches[i] + comparable_fields_counts[i]) / (matches[i] + comparable_fields_counts[i] + non_matches[i]))
    percentage_not_matched.append((non_matches[i] / (matches[i] + comparable_fields_counts[i] + non_matches[i])))
    print(i, "matched:", matches[i], "comparable:", comparable_fields_counts[i], "not matched:", non_matches[i])

reverse engineering matched: 491 comparable: 188 not matched: 223
machine translation matched: 766 comparable: 0 not matched: 134
ethics of artificial intelligence matched: 186 comparable: 302 not matched: 89
post-quantum cryptography matched: 205 comparable: 23 not matched: 50
hardware security matched: 253 comparable: 0 not matched: 227
integrated circuit design matched: 292 comparable: 0 not matched: 430
fairness matched: 164 comparable: 197 not matched: 56
immunotoxicology matched: 142 comparable: 462 not matched: 93
oncogenomics matched: 18 comparable: 5 not matched: 11
biomedical engineering matched: 92 comparable: 0 not matched: 1060
euv lithography matched: 455 comparable: 24 not matched: 58
generative models matched: 6 comparable: 355 not matched: 493
oncolytic virus matched: 65 comparable: 3 not matched: 1
homomorphic encryption matched: 28 comparable: 5 not matched: 3
ellipsometry matched: 7 comparable: 0 not matched: 7
fuzzing matched: 27 comparable: 0 not matched: 3
biomet

In [172]:
print(total_matched, total_comparable + total_matched, total_not_matched)
print(sum(percentage_matched) / len(percentage_matched) * 100, sum(percentage_matched_or_comparable) / len(percentage_matched_or_comparable) * 100, sum(percentage_not_matched) / len(percentage_not_matched) * 100)

146384 211050 26468
47.92961064799904 75.13405577913475 24.86594422086525


In [168]:
non_match_fields["genetic programming"].most_common(10)

[('deep learning', 409),
 ('meta-learning', 243),
 ('neural networks', 228),
 ('active learning', 225),
 ('genetic testing', 223),
 ('transfer learning', 209),
 ('deep reinforcement learning', 205),
 ('biostatistics', 187),
 ('neurorobotics', 184),
 ('neural architecture search', 168)]

In [141]:
# get top 3 fields
i = 0
top_fields_three_only = {}

for row in read_yield_json("../../assets/venues/out/en_scores.jsonl"):
    max_dict = defaultdict(list)
    field_dict = {}
    for field in row["fields"]:
        level = levels[field["id"].lower()]
        max_dict[level].append((field["score"], field["id"]))
    for level in max_dict:
        top_five_fields = sorted(max_dict[level], reverse=True)[:3]
        field_dict[level] = [i[1].lower() for i in top_five_fields]
    top_fields_three_only[row["merged_id"]] = field_dict
    i += 1

In [169]:
# check which fields match when looking at multiple top fields
missing = []
matches = Counter()
non_matches = Counter()
non_match_fields = defaultdict(Counter)
comparable_fields_counts = Counter()
for row in read_yield_json("../../assets/venues/en_venue_fos.jsonl"):
    field_level = levels[row["fos"]]
    # if there was no text we didn't predict so it doesn't appear
    if row["merged_id"] in top_fields_three_only:
        comparable = False
        matched = False
        # print("predicted: ", top_fields[row["merged_id"]][field_level], ", expected: ", row["fos"])
        if row["fos"] in top_fields_three_only[row["merged_id"]][field_level]:
            matches[row["fos"]] += 1
            matched = True
        else: 
            if row["fos"] in comparable_fields:
                for comparable_field in comparable_fields[row["fos"]]:
                    if comparable_field in top_fields_three_only[row["merged_id"]][field_level]:
                        comparable = True
        if comparable:
            comparable_fields_counts[row["fos"]] += 1
        elif not matched:
            non_matches[row["fos"]] += 1
            for non_match_field in top_fields_three_only[row["merged_id"]][field_level]:
                non_match_fields[row["fos"]][non_match_field] += 1
    else:
        missing.append(row["merged_id"])

In [173]:
# getting just the very top field, but in the reverse direction
i = 0
field_links = defaultdict(set)
for row in read_yield_json("../../assets/venues/out/en_scores.jsonl"):
    max_dict = defaultdict(int)
    field_dict = {}
    for field in row["fields"]:
        level = levels[field["id"].lower()]
        if field["score"] > max_dict[level]:
            field_dict[level] = field["id"].lower()
            max_dict[level] = field["score"]
    for field_level in field_dict:
        field_links[field_dict[field_level]].add(row["merged_id"])
    i += 1

In [178]:
ethical_fields = ["ethics of artificial intelligence", "fairness", "regulation of artificial intelligence", "algorithmic bias", "ai safety", "explainable artificial intelligence"]
for field in ethical_fields:
    print(field, ",", len(field_links[field]))

ethics of artificial intelligence , 135
fairness , 653
regulation of artificial intelligence , 167
algorithmic bias , 906
ai safety , 182
explainable artificial intelligence , 372


In [185]:
# read in paper titles

title_map = {}

for row in read_yield_json("../../assets/venues/en_venue_titles.jsonl"):
    if "title_english" in row:
        title_map[row["merged_id"]] = row["title_english"]

In [187]:
for field in ethical_fields:
    i = 0
    print(field)
    print("--------")
    for paper in field_links[field]:
        if i > 10:
            break
        if paper in title_map:
            print(title_map[paper])
            i += 1
    print()

ethics of artificial intelligence
--------
The AI Mirror: Reclaiming our Humanity in an Age of Machine Thinking
Contrastive Language-Vision AI Models Pretrained on Web-Scraped Multimodal Data Exhibit Sexual Objectification Bias
How Sequential Suggestions from a Robot and Human Jury Influence Decision Making: A Large Scale Investigation using a Court Sentencing Judgment Task
Computing Plans that Signal Normative Compliance
On the Distinction between Implicit and Explicit Ethical Agency
How to Write a Good Scientific Paper: Authorship
Lifecycle: A Speculative Fiction on Healthcare Automation
Hard Choices and Hard Limits for Artificial Intelligence
Is NLP Ready for Standardization?
CHATREPORT: Democratizing Sustainability Disclosure Analysis through LLM-based Tools
On the Praxes and Politics of AI Speech Emotion Recognition

fairness
--------
The vocal effort of dominance in scenario meetings
Predicting Fall Probability Based on a Validated Balance Scale
The estimation of direct and indir

In [192]:
biomet_fields = ["biometrics", "deep learning", "activity recognition", "image segmentation", "object detection", "object categorization from image search", "data augmentation", "bioimage informatics", "adversarial machine learning", "one-shot learning", "feature selection"]
for field in biomet_fields:
    print(field, ",", len(field_links[field]))

biometrics , 228
deep learning , 6924
activity recognition , 3202
image segmentation , 6296
object detection , 2733
object categorization from image search , 1421
data augmentation , 912
bioimage informatics , 290
adversarial machine learning , 1502
one-shot learning , 1427
feature selection , 1937


In [193]:
for field in biomet_fields:
    i = 0
    print(field)
    print("--------")
    for paper in field_links[field]:
        if i > 10:
            break
        if paper in title_map:
            print(title_map[paper])
            i += 1
    print()

biometrics
--------
Global features for rapid identity verification with dynamic biometric data
Template protection for HMM-based on-line signature authentication
Seeing Voices and Hearing Faces: Cross-modal biometric matching
What Do You Do When You Know That You Don't Know?
Gender Classification from Iris Images Using Fusion of Uniform Local Binary Patterns
Comparison of quality-based fusion of face and iris biometrics
Facial Landmarking: Comparing Automatic Landmarking Methods with Applications in Soft Biometrics
An investigation of keystroke and stylometry traits for authenticating online test takers
Privacy-Preserving Population-Enhanced Biometric Key Generation from Free-Text Keystroke Dynamics
Biometric Identification and Presentation-Attack Detection using Micro- and Macro-Movements of the Eyes
Real-time personal identification based on haptic information

deep learning
--------
Di-LSTM Contrast : A Deep Neural Network for Metaphor Detection
RT-BENE: A Dataset and Baselines for

In [201]:
# getting just the very top field
i = 0
top_fields_one_only = {}
for row in read_yield_json("../../assets/venues/out/en_scores.jsonl"):
    max_dict = defaultdict(int)
    field_dict = {}
    for field in row["fields"]:
        level = levels[field["id"].lower()]
        if field["score"] > max_dict[level]:
            field_dict[level] = field["id"].lower()
            max_dict[level] = field["score"]
    top_fields_one_only[row["merged_id"]] = field_dict
    i += 1

In [204]:
# check which fields match when looking at just one top field
missing = []
matches = Counter()
non_matches = Counter()
non_match_fields = defaultdict(Counter)
comparable_fields_counts = Counter()
non_match_papers = defaultdict(set)
for row in read_yield_json("../../assets/venues/en_venue_fos.jsonl"):
    field_level = levels[row["fos"]]
    # if there was no text we didn't predict so it doesn't appear
    if row["merged_id"] in top_fields_one_only:
        comparable = False
        matched = False
        # print("predicted: ", top_fields[row["merged_id"]][field_level], ", expected: ", row["fos"])
        if row["fos"] in top_fields_one_only[row["merged_id"]][field_level]:
            matches[row["fos"]] += 1
            matched = True
        elif not matched:
            non_matches[row["fos"]] += 1
            non_match_papers[row["fos"]].add(row["merged_id"])
            non_match_fields[row["fos"]][top_fields_one_only[row["merged_id"]][field_level]] += 1
    else:
        missing.append(row["merged_id"])

In [205]:
# see the most common non-match fields
for i in non_match_fields:
    print(i, "   ", non_match_fields[i].most_common(10))

hardware security     [('cryptography', 101), ('integrated circuit design', 66), ('language-based security', 29), ('network security', 23), ('core ip', 21), ('internet security', 17), ('application security', 16), ('machine learning', 16), ('computer vision', 5), ('biomedical engineering', 4)]
generative models     [('language model', 101), ('text mining', 72), ('automatic summarization', 46), ('dialogue systems', 42), ('parsing', 29), ('question answering', 28), ('semantic parsing', 27), ('machine translation', 25), ('procedural generation', 16), ('algorithmic bias', 16)]
ethics of artificial intelligence     [('fairness', 92), ('regulation of artificial intelligence', 71), ('algorithmic bias', 57), ('ai safety', 49), ('explainable artificial intelligence', 39), ('active learning', 12), ('differential privacy', 10), ('human-robot interaction', 9), ('vehicular automation', 9), ('recommender systems', 9)]
machine translation     [('language model', 41), ('multi-task learning', 28), ('en

In [223]:
cross_disciplinary_fields = ["molecular immunology", "educational neuroscience"]
original_field = "computer simulation"

In [224]:
for field in cross_disciplinary_fields:
    i = 0
    print(field)
    print("--------")
    for paper in field_links[field]:
        if i > 10:
            break
        if paper in title_map and paper in non_match_papers[original_field]:
            print(title_map[paper])
            i += 1
    print()

molecular immunology
--------
Reviews
Reviews
Announcements
Reviews
Reviews
ISAGA News & notes
Editorial: Evaluation
CD-ROM PERIODICAL INDEX - A GUIDE TO ABSTRACTED, INDEXED, AND FULLTEXT PERIODICALS ON CD-ROM - ENSOR,P, HARON,S
Reviews
Reviews
Miscellaneous Reviews

educational neuroscience
--------
Deconstructing Engagement
Leveraging Web-Based Environments for Mass Atrocity Prevention
Theoretical Principles of Simulation-Based Sales Communication Training
The Relation of Entrepreneurship Education to Business Education
Microsimulations: Bridging theory and practice in the composition practicum
Student Ethnocentrism, Dogmatism, and Motivation: A Study of BAFA BAFA
The Minefield Exercise: "The Challenge" in Entrepreneurship Education
A Review of Scholarship on Assessing Experiential Learning Effectiveness
Editorial: Counseling and Counselor Education
Designing Management Education:Practice What You Teach
Ensuring Educational Escape-Room Success: The Process of Designing, Piloting, Eva

In [226]:
# get top 5 fields
i = 0
top_comparison_fields = {}
for row in read_yield_json("../../assets/venues/out/en_comparison_scores.jsonl"):
    max_comparison_dict = defaultdict(list)
    field_comparison_dict = {}
    for field in row["fields"]:
        level = levels[field["id"].lower()]
        max_comparison_dict[level].append((field["score"], field["id"]))
    for level in max_comparison_dict:
        top_five_comparison_fields = sorted(max_comparison_dict[level], reverse=True)[:5]
        field_comparison_dict[level] = [i[1].lower() for i in top_five_comparison_fields]
    top_comparison_fields[row["merged_id"]] = field_comparison_dict
    i += 1

In [277]:
surprise_docs = defaultdict(list)
total_docs = Counter()
for i, row in enumerate(read_yield_json("../../assets/venues/alt/en_venue_comparisons_fos.jsonl")):
    # if there was no text we didn't predict so it doesn't appear
    if row["merged_id"] in top_comparison_fields:
        total_docs[row["fos"]] += 1
        parent_fields = top_comparison_fields[row["merged_id"]][1]
        child_fields = top_comparison_fields[row["merged_id"]][2]
        child_fields.extend(top_comparison_fields[row["merged_id"]][3])
        surprise_fields = set()
        surprise_parents = set()
        for child_field in child_fields:
            if parents[child_field.strip()] in parent_fields:
                surprise_parents.add(parents[child_field.strip()])
                surprise_fields.add(child_field)
        if surprise_fields:
            surprise_docs[row["fos"]].append(row["merged_id"])
            if row["fos"] == "psychology":
                print(row["title_english"])
                # print(row["abstract_english"])
                print(surprise_parents)
                print(surprise_fields)

Exploring Gameful Motivation of Autonomous Learners
{'artificial intelligence'}
{'transfer learning', 'game theory', 'active learning', 'vehicular automation', 'intrinsic motivation', 'machine learning', 'data mining', 'reinforcement learning', 'neuro-symbolic ai', 'robot learning'}
Music Training, Working Memory, and Neural Oscillations: A Review
{'neuroscience'}
{'network neuroscience', 'memory and aging', 'systems neuroscience', 'neural engineering', 'neurorobotics', 'cognitive neuroscience', 'dynamical neuroscience', 'neuroanatomy of memory', 'neuroscience of music'}
Affordances, Adaptive Tool Use and Grounded Cognition
{'artificial intelligence'}
{'markov decision processes', 'fairness', 'machine learning', 'robotics', 'reinforcement learning', 'activity recognition'}
Working Memory and Transcranial-Alternating Current Stimulation—State of the Art: Findings, Missing, and Challenges
{'neuroscience'}
{'network neuroscience', 'memory and aging', 'neurocognition', 'cognitive neuropsyc

In [262]:
for i in surprise_docs:
    print(i, len(surprise_docs[i]), total_docs[i], f"{(len(surprise_docs[i])/total_docs[i]):.2%}")
    

theology 5 485 1.03%
chemistry 653 2860 22.83%
sociology 55 2356 2.33%
psychology 4678 37432 12.50%
statistics 188 5282 3.56%
art history 5 1403 0.36%
architecture 21 447 4.70%
